<a href="https://colab.research.google.com/github/YashashGaurav/EDA-Indian-Startup-Analysis/blob/main/EDA_Notebook.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Problem Domain



Creating a startup is a challenging and exciting endevour. There is so little time to do things that you want to maximize on every step. Especially funding. So we wanted to look at the stature of funding startups in our Home Country: India, and see how it can help an entrepreneure or a VC Fund manager to interact with the market in a more informed manner.


# Dataset

We source our data from 2 Kaggle datasets:
1. [Indian Startups In 2022 - Kaggle](https://www.kaggle.com/datasets/omkargowda/indian-startups-funding-data-januarymay-2022) - The dataset contains datapoints about fundings that various startup in India received for Jan 2022 to May 2022. There are a total of 5 csv files, one for each month.
2. [Indian Startups In 2021 - Kaggle](https://www.kaggle.com/datasets/ramjasmaurya/indian-startupsin-2021) - 
The dataset contains datapoints about fundings that various startup in India received for the year 2021. This year about one thousand successful startup fundings that took place. All the data for this one year is combined into one file that can be loaded onto pandas directly for analysis.

For maps related datafile we use shapefiles as provided openly here: https://github.com/Princenihith/Maps_with_python

For city to state mapping we use openly available JSON data here: https://github.com/nshntarora/Indian-Cities-JSON/blob/master/cities.json which we further add to to need our purpose and can be found in our repo ./dataset/cities.json (we have raised a pull request to the author with our additions)


Imports, and downloads of datasets used:


In [ ]:
! pip install geopandas simpledbf
! git clone https://github.com/Princenihith/Maps_with_python

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
fatal: destination path 'Maps_with_python' already exists and is not an empty directory.


In [ ]:
import io
import requests
import numpy as np
import pandas as pd
import altair as alt
import geopandas as gpd
from simpledbf import Dbf5

In [ ]:
# Downloading the cleaned csv file from our GitHub account
url = "https://raw.githubusercontent.com/YashashGaurav/EDA-Indian-Startup-Analysis/main/dataset/ISF_Consolidated_Final.csv" # Make sure the url is the raw version of the file on GitHub
download = requests.get(url).content

# Reading the downloaded content and turning it into a pandas dataframe
isf_data = pd.read_csv(io.StringIO(download.decode('utf-8')))

# Printing out the first 5 rows of the dataframe
isf_data.head(3)

company_name  founded_year company_hq_location             sector  \
0  CollegeDekho        2015.0            Gurugram         E-Learning   
1          BOX8        2012.0              Mumbai   Food & Beverages   
2         Simpl        2015.0           Bengaluru  Consumer Services   

                                 company_description  \
0  Collegedekho.com is Student’s Partner, Friend ...   
1                   India's Largest Desi Meals Brand   
2  Simpl empowers merchants to build trusted rela...   

                   founders                     investor  amount_usd  \
0              Ruchir Arora             Disrupt ADQ, QIC  35000000.0   
1    Anshul Gupta, Amit Raj                 Tiger Global  40000000.0   
2  Nitya, Chaitra Chidanand  Valar Ventures, IA Ventures  40000000.0   

  funding_round  funding_month  funding_year  
0      Series B             12          2021  
1       Unknown             12          2021  
2      Series B             12          2021

In [ ]:
# for city to state data.
cities = pd.read_json('https://raw.githubusercontent.com/YashashGaurav/EDA-Indian-Startup-Analysis/main/dataset/cities.json')
cities.set_index('id', inplace=True)
cities.head(3)

name        state
id                        
1      Mumbai  Maharashtra
2       Delhi        Delhi
3   Bengaluru    Karnataka

In [ ]:
# for mapping related geo spatial data
gdf = gpd.read_file('./Maps_with_python/india-polygon.shp')
gdf.head(3)

id                        st_nm  \
0  None  Andaman and Nicobar Islands   
1  None            Arunachal Pradesh   
2  None                        Assam   

                                            geometry  
0  MULTIPOLYGON (((93.84831 7.24028, 93.92705 7.0...  
1  POLYGON ((95.23643 26.68105, 95.19594 27.03612...  
2  POLYGON ((95.19594 27.03612, 95.08795 26.94578...

# Analysis: in a QnA format

## Question 1

`Where should budding entrepreneurs in their respective sectors move to, to have the most vacitnity to successful startups?`

### Preparing data for analysis

1. Removing rows that don't have an Indian State.
2. Removing rows that don't have 'undisclosed', 'unavailable' amount_usd values \
and convert the numbers to float
3. Removing NaN state value rows
4. Remove undisclosed funding rows

In [ ]:
# Loading the dataset
isfd_with_state = isf_data.merge(cities, how='left', left_on='company_hq_location', right_on='name').drop(['name'], axis=1)
isfd_with_state = isfd_with_state.rename(columns={'state': 'company_hq_state'})
isfd_with_state['company_hq_state'].value_counts()

Karnataka                 568
Maharashtra               336
Haryana                   222
Delhi                     178
Tamil Nadu                 72
Uttar Pradesh              55
Telangana                  50
Gujarat                    33
Rajasthan                  20
Kerala                      9
West Bengal                 8
Chandigarh                  6
Madhya Pradesh              3
Goa                         3
Andhra Pradesh              2
Bihar                       2
Jharkhand                   2
Assam                       2
Uttarakhand                 1
Dadra and Nagar Haveli      1
Odisha                      1
Maharastra                  1
Name: company_hq_state, dtype: int64

In [ ]:
# Analysing the effect of dropping states with no names
print(f'By dropping we lose: {isfd_with_state["company_hq_state"].isna().sum() / len(isfd_with_state):.04f}% data')

By dropping we lose: 0.0290% data


In [ ]:
# remove NaN states
isfd_with_state = isfd_with_state.dropna(subset=["company_hq_state"])

In [ ]:
# Identify how many rows are 'undisclosed'/'unavailable'
isfd_with_state[isfd_with_state['amount_usd'].str.isalpha()]["amount_usd"].value_counts()

undisclosed    163
unavailable     11
Name: amount_usd, dtype: int64

In [ ]:
# drop 'undisclosed'/'unavailable' funding amount
isfd_with_state['amount_usd'] = isfd_with_state['amount_usd'].replace({'undisclosed': np.nan, 'unavailable': np.nan})
isfd_with_state = isfd_with_state.dropna(subset=['amount_usd'])
# making all the values in amount_usd as float
isfd_with_state['amount_usd'] = isfd_with_state['amount_usd'].astype(float)
len(isfd_with_state)

1401

### Graph wise data preparation, Graphing and preliminary analysis

In [ ]:
background_map = alt.Chart(gdf).mark_geoshape(
    stroke='grey',
    strokeWidth=0.5,
    fill='lightgrey'
)

#### Statewise distribution of funding amounts:

In [ ]:
state_sector_sum_group = isfd_with_state.groupby(['company_hq_state', 'sector'])['amount_usd'].sum().reset_index()
state_sector_sum_group['amount_usd_millions'] = state_sector_sum_group['amount_usd'] / 10**6
state_sector_sum_group.head(5)

company_hq_state      sector  amount_usd  amount_usd_millions
0   Andhra Pradesh      Retail   6300000.0                  6.3
1            Bihar    Agritech  33000000.0                 33.0
2       Chandigarh    Agritech  21000000.0                 21.0
3       Chandigarh          Ai    200000.0                  0.2
4       Chandigarh  Automotive  28000000.0                 28.0

In [ ]:
# setting up the graph that shows histographic representation of 
# funding distribution
histogram_state_wise_funding = alt.Chart(
    state_sector_sum_group).mark_bar().transform_aggregate(
        sum_funding='sum(amount_usd_millions)',
        groupby=['company_hq_state']
    ).encode(
        y=alt.Y("sum_funding:Q", title='Sum of funding ($, Millions)'),
        x=alt.X('company_hq_state', sort='-y', title='Company HQ States'),
        tooltip=['sum_funding:Q']
    ).properties(
        width=800,
        title='State wise distribution of funding raised by startups of that state'
    )

In [ ]:
# Aggregating data for map's purposes
agg_map_data = (
    state_sector_sum_group.groupby(["company_hq_state"])[
        "amount_usd_millions"
    ]
    .sum()
    .reset_index()
)
agg_map_data['amount_usd_percentage'] = agg_map_data['amount_usd_millions']/agg_map_data['amount_usd_millions'].sum()

# merge with geopandas
gdf_state_sum = gdf.merge(agg_map_data, left_on='st_nm', right_on='company_hq_state')
gdf_state_sum.head(3)

id                   st_nm  \
0  None                   Bihar   
1  None              Chandigarh   
2  None  Dadra and Nagar Haveli   

                                            geometry        company_hq_state  \
0  POLYGON ((88.11357 26.54028, 88.28006 26.37640...                   Bihar   
1  POLYGON ((76.84208 30.76124, 76.83758 30.72552...              Chandigarh   
2  POLYGON ((73.20640 20.12165, 73.20865 20.10695...  Dadra and Nagar Haveli   

   amount_usd_millions  amount_usd_percentage  
0                 33.0               0.000491  
1                 52.1               0.000776  
2                  1.0               0.000015

In [ ]:
# map that shows all data aggregated
aggregate_map = alt.Chart(gdf_state_sum).mark_geoshape(
    stroke='grey',
    strokeWidth=1,
).encode(
    tooltip=[
        alt.Tooltip('st_nm:N', title='State'), 
        alt.Tooltip('amount_usd_millions:Q', title='Funding Amount ($, Millions)'),
        alt.Tooltip('amount_usd_percentage:Q', format='.2%', title='Funding Percentage')],
    color=alt.Color('amount_usd_millions:Q', title='Funding Amount ($, Millions)')
).properties(
    width=800,
    height=500,
    title='Distribution of startup funding money across India'
)

(background_map + aggregate_map) & histogram_state_wise_funding

alt.VConcatChart(...)

Figure Above: 
1. Map of India with states color coded with sum of funding amount for that state. 
2. Histogram showing distribution of funding availed by different states across India

`Analysis`: We understand that there is alsmot an exponentially decreasing distribution of funding across the country. With just at an aggregate most successful startups that raise funding are from Karnataka and Maharashtra.

#### Sector wise distribution of funding amount across states

In [ ]:
# munging data for the analysis
state_sector_sum_group = isfd_with_state.groupby(['company_hq_state', 'sector'])['amount_usd'].sum().reset_index()
state_sector_sum_group['amount_usd_millions'] = state_sector_sum_group['amount_usd'] / 10**6
state_sector_sum_group

company_hq_state               sector  amount_usd  amount_usd_millions
0     Andhra Pradesh               Retail   6300000.0                  6.3
1              Bihar             Agritech  33000000.0                 33.0
2         Chandigarh             Agritech  21000000.0                 21.0
3         Chandigarh                   Ai    200000.0                  0.2
4         Chandigarh           Automotive  28000000.0                 28.0
..               ...                  ...         ...                  ...
523      West Bengal               Edtech   7500000.0                  7.5
524      West Bengal     Food & Beverages  15000000.0                 15.0
525      West Bengal           Healthcare   3000000.0                  3.0
526      West Bengal  Metal Manufacturing   2400000.0                  2.4
527      West Bengal               Retail   4000000.0                  4.0

[528 rows x 4 columns]

In [ ]:
alt.Chart(state_sector_sum_group).mark_bar().encode(
    y=alt.Y("sum(amount_usd_millions):Q", title='Funding Amount ($, Millions)'),
    x=alt.X('sector', sort='-y', title='Sectors'),
    color='company_hq_state:N',
    tooltip=[
        alt.Tooltip('sum(amount_usd_millions):Q', title='Funding Amount'),
        alt.Tooltip('company_hq_state:N', title='State'),
    ]
).properties(
    title=''
)

alt.Chart(...)

In [ ]:
gdf_state_sector_sum = pd.merge(gdf, state_sector_sum_group, left_on='st_nm', right_on='company_hq_state', how='right')
gdf_state_sector_sum.head()

id           st_nm                                           geometry  \
0  None  Andhra Pradesh  POLYGON ((81.10545 17.82313, 81.39342 17.81473...   
1  None           Bihar  POLYGON ((88.11357 26.54028, 88.28006 26.37640...   
2  None      Chandigarh  POLYGON ((76.84208 30.76124, 76.83758 30.72552...   
3  None      Chandigarh  POLYGON ((76.84208 30.76124, 76.83758 30.72552...   
4  None      Chandigarh  POLYGON ((76.84208 30.76124, 76.83758 30.72552...   

  company_hq_state      sector  amount_usd  amount_usd_millions  
0   Andhra Pradesh      Retail   6300000.0                  6.3  
1            Bihar    Agritech  33000000.0                 33.0  
2       Chandigarh    Agritech  21000000.0                 21.0  
3       Chandigarh          Ai    200000.0                  0.2  
4       Chandigarh  Automotive  28000000.0                 28.0

In [ ]:
sector_dropdown = alt.binding_select(
    options= [None] + sorted(list(state_sector_sum_group["sector"].unique())),
    labels= ['All'] + sorted(list(state_sector_sum_group["sector"].unique())),
    name="select_sector",
)
sector_select = alt.selection_single(
    fields=["sector"], bind=sector_dropdown, name="Sector"
)

sector_wise_map = alt.Chart(gdf_state_sector_sum).mark_geoshape(
    stroke='grey',
    strokeWidth=0.5
).encode(
    tooltip=[
        alt.Tooltip('company_hq_state:N', title='State'), 
        alt.Tooltip('sector:N', title='Sector'), 
        alt.Tooltip('amount_usd_millions:Q', title='Funding Amount ($, Millions)')
    ],
    color=alt.Color('amount_usd_millions:Q', title='Funding Amount ($, Millions)')
).add_selection(
    sector_select
).transform_filter(
    sector_select
).properties(
    width=800,
    height=800,
    title='Sector Wise Funding Distribution'
)

background_map + sector_wise_map

alt.LayerChart(...)

Figure Above: Sector wise selector that allows one to look at the country and its states where the states are color coded by the sum of funding availed in that state

`Analysis`: For every sector, we see the distribution of funding amount raising companies vary greatly. There are areas where some kinds of industries do not exist and have not shown to raise money from.

### Answering question one:

We find that different sectors not only get funded differently, they also have a certain presence in certain localities. For example:

We see 'Financial Serivices' startup sector is predominantly based out of Karnataka, Uttar Pradesh, Delhi and Haryana. So, it would be beneficial for me to be in these locations as their seems to be a greater visibility of these sectors from HQ-ed at these locations

## Question 2

`As an entrepreneur, I want to know the distribution of funds across my sector in different funding rounds. This will give me statistical edge while pitching for further funding and negotiating offers.`



### Preparing data for analysis

In [ ]:
## clean amount_usd column
isf_data_2 = isf_data.copy(deep=True)
# remove undisclosed and unavailable.
isf_data_2['amount_usd'] = isf_data_2['amount_usd'].replace({'undisclosed': np.nan, 'unavailable': np.nan})
isf_data_2 = isf_data_2.dropna(subset=['amount_usd'])
# change entries to floats
isf_data_2['amount_usd'] = isf_data_2['amount_usd'].astype(float)
isf_data_2['amount_usd_millions'] = isf_data_2['amount_usd']/10**6

isf_data_2.head(3)

company_name  founded_year company_hq_location             sector  \
0  CollegeDekho        2015.0            Gurugram         E-Learning   
1          BOX8        2012.0              Mumbai   Food & Beverages   
2         Simpl        2015.0           Bengaluru  Consumer Services   

                                 company_description  \
0  Collegedekho.com is Student’s Partner, Friend ...   
1                   India's Largest Desi Meals Brand   
2  Simpl empowers merchants to build trusted rela...   

                   founders                     investor  amount_usd  \
0              Ruchir Arora             Disrupt ADQ, QIC  35000000.0   
1    Anshul Gupta, Amit Raj                 Tiger Global  40000000.0   
2  Nitya, Chaitra Chidanand  Valar Ventures, IA Ventures  40000000.0   

  funding_round  funding_month  funding_year  amount_usd_millions  
0      Series B             12          2021                 35.0  
1       Unknown             12          2021                 40.0  
2      Series B             12          2021                 40.0

In [ ]:
# Clean funding_round data
isf_data_2['funding_round'] = isf_data_2['funding_round'].replace({'Unknown': np.nan})
isf_data_2 = isf_data_2.dropna(subset=['funding_round'])

sorted(isf_data_2['funding_round'].unique())

['Angel',
 'Bridge',
 'Debt',
 'Post-Seed',
 'Pre-Seed',
 'Pre-Series A',
 'Pre-Series B',
 'Seed',
 'Series A',
 'Series B',
 'Series C',
 'Series D',
 'Series E',
 'Series F',
 'Series G',
 'Series H',
 'Series I',
 'Series J',
 'Series S',
 'Undisclosed']

In [ ]:
# Cleaning sectoral data
isf_data_2['sector'] = isf_data_2['sector'].replace({'Unknown': np.nan})
isf_data_2 = isf_data_2.dropna(subset=['sector'])

### Graphs and preliminary analysis

In [158]:
# Dropdown selector for sector
sector_dropdown = alt.binding_select(
    options=[None] + sorted(list(isf_data_2["sector"].unique())),
    labels = ['All'] + sorted(list(isf_data_2["sector"].unique())),
    name="Select Sector ",
)
sector_select = alt.selection_single(
    fields=["sector"], bind=sector_dropdown, name="Sector"
)

funding_round_select = alt.selection(type="multi", fields=['funding_round'])

# Click event selector for Funding Round
base_chart = alt.Chart(isf_data_2).mark_bar().encode(
    x=alt.X('sector:N', sort='-y'),
    y='amount_usd_millions:Q',
    color= alt.Color(
        'funding_round:N',
        sort=sorted(isf_data_2['funding_round'].unique())
    ),
    tooltip=[
        alt.Tooltip('funding_round:N', title='Funding Round'),
        alt.Tooltip('amount_usd_millions:N', title='Funding'),
        alt.Tooltip('company_name:N', title='Company Name'),
        alt.Tooltip('investor:N', title='Investor')
    ],
)

sector_wise_chart = (
    base_chart.add_selection(sector_select).add_selection(funding_round_select)
    .transform_filter(sector_select).transform_filter(funding_round_select)
    .properties(title="Sector Wise Funding Distribution", height=500)
    .add_selection(funding_round_select)
)

sector_wise_chart

alt.Chart(...)

Figure Above: Histographic distribution of funding amount of data grouped by sectors and colour coded by funding round


`Analysis`: We again witness that every sector and funding round have vastly different funding strategies. Building on our example above, let us say I am a company that is in the 'Financial Services' sector and I am ready for Series C funding, I can see that it is not uncommon to raise from \$30M to \$300M! Given which investor I approach I can make a more informed decision of the amount of funding I can pitch for (or maybe aim for a pre-series funding before a Series C filing just to make sure my company is valued well before investment)

## Question 3

`Suppose you are trying to determine the right time to seek funding in your respective sector. What are the best months that typically receive the highest funding?` 

### Preparing data for analysis

In [161]:
#There are multiple 'funding_round' values that exist which will not fit on a single graph
#Identify the most common occurring 'funding_round' values
isf_data['funding_round'].value_counts().head(25)

Unknown         540
Seed            320
Pre-Series A    199
Series A        183
Series B         75
Series C         65
Pre-Seed         58
Series D         37
Undisclosed      37
Series E         29
Debt             26
Series F         21
Pre-Series B     11
Series H          5
Series G          5
Bridge            2
Series I          2
Series J          2
Series S          1
Post-Seed         1
Angel             1
Name: funding_round, dtype: int64

In [162]:
#Based on value_counts summary, only select 'funding_round' values where there are at least 20 instances
isf_data['funding_round'].value_counts()[isf_data['funding_round'].value_counts() >= 20]

Unknown         540
Seed            320
Pre-Series A    199
Series A        183
Series B         75
Series C         65
Pre-Seed         58
Series D         37
Undisclosed      37
Series E         29
Debt             26
Series F         21
Name: funding_round, dtype: int64

In [163]:
#Select list of series types that we are interested in
series_list = ['Pre-Seed', 
               'Seed', 
               'Pre-Series A', 
               'Series A', 
               'Series B',
               'Series C', 
               'Series D', 
               'Series E',
               'Series F',
               'Debt',
               'Undisclosed',
               'Unknown'
            ]

In [164]:
#Filter isf_data to only account for 'funding_round' values present in series_list defined above
isf_consolidated_fr_filtered_final = isf_data[isf_data['funding_round'].isin(series_list)]

### Graphs and preliminary analysis

In [176]:
#Get a list of all sectors in our dataset, which represents the drop-down criteria for the altair plot
all_sector_list = isf_consolidated_fr_filtered_final['sector'].value_counts().index.tolist()

select_box = alt.binding_select(
    options=[None] + all_sector_list, labels = ['All'] + all_sector_list
)
selection = alt.selection_single(
    fields=['sector'], bind=select_box, name='Financial Sector'
)

#create a grouped bar chart
alt.Chart(
        isf_consolidated_fr_filtered_final, 
        title = 'Aggregate Totals For Each Funding Round'
    ).mark_bar().encode(
        x=alt.X('funding_round:N', sort = series_list, title = 'Funding Round'),
        y=alt.Y('count(funding_round):Q', title = 'Aggregate Totals'),
        color='funding_round:N'
    ).add_selection(
        selection
    ).transform_filter(
        selection
    ).properties(
        width=800,
        height=400
    )

alt.Chart(...)

### Answering Question 3:

There are many insights that can be generated when filtering the bar graph above into different finanial sectors:



1. The Financial Services sector seems to be the most predominant one in India due to the number of rounds of funding that exists.
2. The Food & Beverages sector is a close second! Investors seem to be confident in this sector as well as there have been 10 rounds of funding.

1.   The Hospital & Health Care sector does not seem to have as much traction in India, as there hve only been 6 rounds of funding into this sector
2.   The Aviation & Aerospace sector only has 2 rounds of funding among investors, indicating that investors tend to shy away from this area.






## Question 4

`Suppose your goal is to invest in small startup companies. What kind of sectors receive multiple rounds of funding?`

`More funding leads to better exits and increased profits.`

### Preparing data for analysis

In [169]:
#Get the total number of distinct sectors in our population
print ("Total number of distinct sectors - {}\n".format(len(pd.unique(isf_data['sector']))))

Total number of distinct sectors - 249



In [170]:
#There are 249 values in the "sector" column which cannot be plotted on a single graph
#Therefore, get the 20 most popular sectors in India and put values in a list 
common_sector_list = isf_data['sector'].value_counts().head(20).index.tolist()

In [171]:
#Filter isf_consolidated based on common_sector_list
isf_consolidated_sector_filtered = isf_data[isf_data['sector'].isin(common_sector_list)]

In [172]:
#Remove NaN values from "amount_usd" column
isf_consolidated_sector_filtered = isf_consolidated_sector_filtered.dropna(subset=['amount_usd'])

In [173]:
#Filter out records that are non-numerical in "amount_usd" (e.g. undisclosed, unavailable)
isf_consolidated_sector_filtered = isf_consolidated_sector_filtered[~isf_consolidated_sector_filtered['amount_usd'].str.isalnum()]

### Graphs and preliminary analysis

In [175]:
#Create a drop-down criteria for the altair plot
select_box_2 = alt.binding_select(
    options=[None] + common_sector_list, labels = ['All'] + common_sector_list)
selection = alt.selection_single(fields=['sector'], bind=select_box_2, name='financial')


#For the line plot, have "funding_month" on x-axis and average of "amount_usd" on y-axis
alt.Chart(isf_consolidated_sector_filtered, title = 'Average Amount of Funding Given By Investors Per Month').mark_line().encode(
    x=alt.X('funding_month', title = 'Funding Month'),
    color='sector',
    y=alt.Y('mean(amount_usd):Q', title = 'Average Funding Amount ($)')
).add_selection(
    selection
).transform_filter(
    selection
).properties(
    width=800,
    height=500
)

alt.Chart(...)

### Answering Question 4:

Generally, many sectors receive funding in the month of April as indicated by various peaks on the line graph.

However, many more insights can be generated when analyzing the data by certain financial sectors:



1.   For the Automotive sector, the best months to seek funding are April and September.
2.   For the Retail sector, entrepreneurs should aim to seek funding during the month of July.

1.   The months of March, May, and December are entrepreneuer's best hopes to receive funding. 
2.   For the Logistics & Supply Chain sector, entrepreneuers can expect to receive funding during the months of January, April, and October. 







# Key Findings

##### Entrepreneurs:
The states Karnataka, Maharashtra, and Haryana are prime spots to relocate to get funding.

In general, April is typically a great month for companies to acquire funding. However, different sectors perform well during different time periods of the year. 
In your case, It is April as well!


##### Investors:
Many investors are confident about the direction of the Financial Services sector currently, as evidenced by the multiple rounds of funding provided to entrepreneurs.

It is usually the case that certain sectors perform better is different locations that others. You should stay in Karnataka though. 

In [166]:
print('_ fin _')

_ fin _
